In [12]:
import pandas as pd
import numpy as np
from tqdm.notebook import tqdm

In [2]:
ddi = pd.read_csv('raw/Drugbank_drug_interactions.tsv', sep='\t', index_col=0)
ddi

C:\Users\Notebook\anaconda3\lib\site-packages\numpy\lib\arraysetops.py:583: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  mask |= (ar1 == a)


drug id                drug name interaction drug id  \
0        DB00001                Lepirudin             DB06605   
1        DB00001                Lepirudin             DB06695   
2        DB00001                Lepirudin             DB01254   
3        DB00001                Lepirudin             DB01609   
4        DB00001                Lepirudin             DB01586   
...          ...                      ...                 ...   
2768186  DB16746  Elivaldogene autotemcel             DB01264   
2768187  DB16746  Elivaldogene autotemcel             DB01319   
2768188  DB16746  Elivaldogene autotemcel             DB01601   
2768189  DB16746  Elivaldogene autotemcel             DB11586   
2768190  DB16746  Elivaldogene autotemcel             DB15623   

        interaction drug name  \
0                    Apixaban   
1        Dabigatran etexilate   
2                   Dasatinib   
3                 Deferasirox   
4        Ursodeoxycholic acid   
...                       ...   
2768186             Darunavir   
2768187         Fosamprenavir   
2768188             Lopinavir   
2768189           Asunaprevir   
2768190            TMC-310911   

                                               description  
0        Apixaban may increase the anticoagulant activi...  
1        Dabigatran etexilate may increase the anticoag...  
2        The risk or severity of bleeding and hemorrhag...  
3        The risk or severity of gastrointestinal bleed...  
4        The risk or severity of bleeding and bruising ...  
...                                                    ...  
2768186  The therapeutic efficacy of Elivaldogene autot...  
2768187  The therapeutic efficacy of Elivaldogene autot...  
2768188  The therapeutic efficacy of Elivaldogene autot...  
2768189  The therapeutic efficacy of Elivaldogene autot...  
2768190  The therapeutic efficacy of Elivaldogene autot...  

[2768191 rows x 5 columns]

In [3]:
drug1s = ddi['drug id']
drug2s = ddi['interaction drug id']
drugs = pd.concat([drug1s, drug2s], axis=0).unique()
drugs

array(['DB00001', 'DB00002', 'DB00004', ..., 'DB09047', 'DB11074',
       'DB00878'], dtype=object)

In [4]:
print(len(drug1s.unique()))
print(len(drug2s.unique()))
len(drugs)

4417
4418


5915

In [10]:
# assign node index to drugs
data = []
for idx, drug in enumerate(drugs):
    data.append([drug,idx])

data = np.asarray(data)
drug_id_df = pd.DataFrame({'DrugBank_id': data[:,0], 'node_index': data[:,1]})
drug_id_df

5915it [00:00, 2353154.53it/s]


DrugBank_id node_index
0        DB00001          0
1        DB00002          1
2        DB00004          2
3        DB00005          3
4        DB00006          4
...          ...        ...
5910     DB12264       5910
5911     DB06614       5911
5912     DB09047       5912
5913     DB11074       5913
5914     DB00878       5914

[5915 rows x 2 columns]

In [6]:
drug_id_df.to_csv('raw/drug2id.tsv',sep='\t',index=False) # save drug2id file

In [16]:
edge_indexes = []
drug1_prev = drug2_prev = ''
drug1_idx = drug2_idx = 0
for index, row in tqdm(ddi.iterrows(), total = len(ddi)):
    drug1 = row['drug id']
    drug2 = row['interaction drug id']
    if drug1 != drug1_prev:
        drug1_idx = drug_id_df.index[drug_id_df['DrugBank_id'] == drug1][0]

    if drug2 != drug2_prev:
        drug2_idx = drug_id_df.index[drug_id_df['DrugBank_id'] == drug2][0]
        
    edge_indexes.append([drug1_idx,drug2_idx])
    edge_indexes.append([drug2_idx,drug1_idx]) # the graph is not directed
    
    drug1_prev = drug1
    drug2_prev = drug2

  0%|          | 0/2768191 [00:00<?, ?it/s]

In [19]:
edge_indexes = np.asarray(edge_indexes)
drug_interaction_df = pd.DataFrame({'drug1_idx': edge_indexes[:,0], 'drug2_idx': edge_indexes[:,1]})
drug_interaction_df

drug1_idx  drug2_idx
0                0       2022
1             2022          0
2                0       4417
3             4417          0
4                0       4418
...            ...        ...
5536377       1358       4416
5536378       4416       2891
5536379       2891       4416
5536380       4416       4329
5536381       4329       4416

[5536382 rows x 2 columns]

In [20]:
drug_interaction_df.to_csv('raw/drug_interactions.tsv',sep='\t',index=False) # save drug_interactions file